### SQL2Circuits development notebook

In [1]:
import os
from data_preparation.queries import QueryGenerator
from data_preparation.prepare import DataPreparation
from data_preparation.database import Database
from circuit_preparation.circuits import Circuits
import jax
from training.train import SQL2CircuitsEstimator
import itertools
jax.config.update("jax_enable_x64", True)

this_folder = os.path.abspath(os.getcwd())
seed_paths = ["data_preparation//query_seeds//JOB_query_seed_execution_time.json",
              "data_preparation//query_seeds//JOB_query_seed_cardinality.json"]
workload_types = ["execution_time", "cardinality"]
run_id = 1
ty = 1
workload_type = workload_types[ty]
database = Database("IMDB")
generator = QueryGenerator(run_id, workload_type = "cardinality", database = "IMDB", query_seed_file_path = seed_paths[ty])
query_file = generator.get_query_file()
data_preparator = DataPreparation(run_id, query_file, database = database, workload_type = workload_type, classification = 2)


Number of training queries is  398
Number of test queries is  140
Number of validation queries is  135
cardinality
Error while fetching data from PostgreSQL connection to server at "localhost" (127.0.0.1), port 5432 failed: Connection refused
	Is the server running on that host and accepting TCP/IP connections?

{'2': 969831, '3': 2288576, '4': 52494222, '7': 21027170, '8': 2447042, '9': 577409, '11': 0, '12': 37545, '15': 479596, '20': 2866, '24': 5542, '25': 21219, '26': 811831, '30': 29757, '32': 257934, '34': 1413783, '35': 1626450, '37': 243288, '40': 2407523, '41': 68258, '43': 68258, '44': 1697156, '46': 2449481, '47': 559065, '48': 99094, '51': 0, '52': 488912, '53': 2288639, '54': 969837, '56': 52501982, '57': 102555254, '59': 21028934, '61': 577460, '64': 2669657, '65': 1572370, '66': 2669657, '67': 10827927, '68': 32397582, '70': 3182571, '71': 752392, '74': 0, '75': 683930, '82': 37545, '83': 14104, '85': 479596, '89': 35773, '91': 45270, '92': 0, '97': 1512771, '99': 25632

In [2]:
this_folder = os.path.abspath(os.getcwd())
output_folder = this_folder + "//circuit_preparation//data//circuits//" + str(run_id) + "//"
if not os.path.exists(output_folder):
    os.makedirs(output_folder)
    print("The new directory: ", output_folder, " is created.")

circuits = Circuits(run_id, query_file, output_folder, write_cfg_to_file = True, write_pregroup_to_file=True, generate_circuit_png_diagrams = True)
circuits.execute_full_transformation()

In [3]:
from training.utils import construct_data_and_labels, select_circuits

optimization_interval = 20
init_n_of_circuits = 10

training_data = data_preparator.get_training_data()
validation_data = data_preparator.get_validation_data()
test_data = data_preparator.get_test_data()

training_classes = data_preparator.get_training_data_labels()
validation_classes = data_preparator.get_validation_data_labels()
test_classes = data_preparator.get_test_data_labels()

circuits.select_circuits_with_data_point(training_data, validation_data, test_data)

# Training, validation and test circuits
training_circuits = circuits.get_training_circuits()
validation_circuits = circuits.get_validation_circuits()
test_circuits = circuits.get_test_circuits()

# Select the first 10 circuits
current_training_circuits = dict(itertools.islice(training_circuits.items(), init_n_of_circuits))
current_validation_circuits = select_circuits(current_training_circuits, validation_circuits, init_n_of_circuits)
current_test_circuits = select_circuits(current_training_circuits, test_circuits, init_n_of_circuits)

# Construct the data and labels for the training, validation and test circuits
training_circuits_X, training_labels_y = construct_data_and_labels(current_training_circuits, training_classes)
validation_circuits_X, validation_labels_y = construct_data_and_labels(current_validation_circuits, validation_classes)
test_circuits_X, test_labels_y = construct_data_and_labels(current_test_circuits, test_classes)

X_train = list(zip(training_circuits_X, training_labels_y))
X_valid = list(zip(validation_circuits_X, validation_labels_y))
y = [(circ, ) for circ in test_circuits_X]

In [4]:
trainer = SQL2CircuitsEstimator(run_id, 
                              workload = "cardinality", 
                              a = 0.001, 
                              c = 0.001, 
                              classification = 2, 
                              optimization_method = "SPSA")
trainer.fit(X_train, y, X_valid = X_valid)

id: 1
a: 0.001
c: 0.001
epochs: 1000
classification: 4
workload: cardinality
optimization_medthod: SPSA



Initializing new parameters
10 10


[[[0.19622516 0.31067676]
  [0.1908816  0.30221647]]

 [[0.4631932  0.09936826]
  [0.36017141 0.07726714]]

 [[0.08531964 0.11641461]
  [0.33761113 0.46065462]]

 ...

 [[0.30909446 0.37781228]
  [0.14088578 0.17220748]]

 [[0.09898675 0.10274735]
  [0.39169256 0.40657334]]

 [[0.2991915  0.31055807]
  [0.19148781 0.19876262]]]
[[0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [1, 0, 0, 0], [0, 0, 1, 0], [0, 0, 1, 0], [0, 1, 0, 0]]
[0.19622516 0.31067676 0.1908816  0.30221647] [0 0 0 1]
4 4
[0.4631932  0.09936826 0.36017141 0.07726714] [0 0 0 1]
4 4
[0.08531964 0.11641461 0.33761113 0.46065462] [0 0 0 1]
4 4
[0.2533512  0.34568592 0.16957952 0.23138336] [0 0 0 1]
4 4
[0.20499402 0.2797048  0.2179367  0.29736448] [0 0 0 1]
4 4
[0.25788182 0.35186774 0.1650489  0.22520154] [0 0 0 1]
4 4
[0.51946163 0.07957548 0.34769938 0.05326351] [1 0 0 0]
4 4
[0.30909446 0.37781228 0.14088578 0.17220748] [0 0 1 0]
4 4
[0.09898675 0.10274735 0.39169256 0.40657334] [0 

iters: 20
train/loss: 2.9459
train/acc: 0.3
valid/loss: 2.8888
valid/acc: 0.0



[0.29964695 0.23460248 0.26122767 0.2045229 ] [0 0 0 1]
4 4
[0.05436417 0.22743926 0.13855082 0.57964576] [0 0 0 1]
4 4
[0.11059399 0.46268521 0.08232072 0.34440007] [0 0 0 1]
4 4
[0.09698238 0.4057391  0.09593235 0.40134616] [0 0 0 1]
4 4
[0.11068522 0.46306688 0.0822295  0.3440184 ] [0 0 0 1]
4 4
[0.43794827 0.13533093 0.32598712 0.10073368] [1 0 0 0]
4 4
[0.30477176 0.36649423 0.14925357 0.17948044] [0 0 1 0]
4 4
[0.12684685 0.15495642 0.32327869 0.39491804] [0 0 1 0]
4 4
[0.25826047 0.31549163 0.19186506 0.23438283] [0 1 0 0]
4 4
[[[0.09316614 0.47862255]
  [0.06977192 0.35843938]]

 [[0.2554579  0.3163308 ]
  [0.19131186 0.23689944]]

 [[0.22437338 0.27783918]
  [0.22239637 0.27539106]]

 ...

 [[0.42759219 0.1441965 ]
  [0.32022286 0.10798845]]

 [[0.42623233 0.14373791]
  [0.32158272 0.10844703]]

 [[0.48537114 0.05154573]
  [0.41862567 0.04445746]]]
[[0, 0, 0, 1], [0, 0, 1, 0], [0, 0, 1, 0], [0, 1, 0, 0], [0, 0, 1, 0], [0, 1, 0, 0], [0, 1, 0, 0]]
[0.09316614 0.47862255 0.069771

...

[0.00110042 0.0398328  0.02577597 0.93329082] [0 0 0 1]
4 4
[0.01349918 0.48878091 0.01337663 0.48434328] [0 0 0 1]
4 4
[0.01311503 0.47487112 0.01376079 0.49825307] [0 0 0 1]
4 4
[0.01292844 0.46811535 0.01394737 0.50500884] [0 0 0 1]
4 4
[0.42139907 0.08088103 0.41757319 0.08014671] [1 0 0 0]
4 4
[0.26994255 0.24001704 0.25939851 0.2306419 ] [0 0 1 0]
4 4
[0.01797696 0.0229558  0.4212055  0.53786173] [0 0 1 0]
4 4
[0.21126599 0.2697778  0.22791646 0.29103975] [0 1 0 0]
4 4
[[[3.39212946e-02 4.37295817e-01]
  [3.80652533e-02 4.90717635e-01]]

 [[2.48053333e-01 2.31400361e-01]
  [2.69313279e-01 2.51233027e-01]]

 [[6.15942502e-05 8.77731863e-03]
  [6.86794303e-03 9.84293144e-01]]

 ...

 [[2.69950234e-01 2.39553875e-01]
  [2.59879122e-01 2.30616769e-01]]

 [[3.89379899e-03 4.94458266e-03]
  [4.36660724e-01 5.54500894e-01]]

 [[2.11715163e-01 2.68850037e-01]
  [2.28839341e-01 2.90595460e-01]]]
[[0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [1, 0, 0,

iters: 980
train/loss: 2.1447
train/acc: 0.5
valid/loss: 3.0587
valid/acc: 0.0



[[[4.43883263e-02 4.26509687e-01]
  [4.98748130e-02 4.79227174e-01]]

 [[2.43924525e-01 2.34744899e-01]
  [2.65664166e-01 2.55666410e-01]]

 [[6.40587384e-04 4.34647218e-02]
  [1.38772242e-02 9.42017467e-01]]

 ...

 [[2.69903504e-01 2.36018061e-01]
  [2.63585327e-01 2.30493109e-01]]

 [[1.97490511e-02 2.43558294e-02]
  [4.28025520e-01 5.27869600e-01]]

 [[2.14471889e-01 2.64501036e-01]
  [2.33302667e-01 2.87724408e-01]]]
[[0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [0, 0, 0, 1], [1, 0, 0, 0], [0, 0, 1, 0], [0, 0, 1, 0], [0, 1, 0, 0]]
[0.04438833 0.42650969 0.04987481 0.47922717] [0 0 0 1]
4 4
[0.24392452 0.2347449  0.26566417 0.25566641] [0 0 0 1]
4 4
[6.40587384e-04 4.34647218e-02 1.38772242e-02 9.42017467e-01] [0 0 0 1]
4 4
[0.00727303 0.49371973 0.00724421 0.49176303] [0 0 0 1]
4 4
[0.00707915 0.48055767 0.0074381  0.50492507] [0 0 0 1]
4 4
[0.00695337 0.47201956 0.00756387 0.5134632 ] [0 0 0 1]
4 4
[0.42638645 0.07460631 0.4246966  0.07431063] [1 0 0 0]
4

iters: 1000
train/loss: 2.1561
train/acc: 0.5
valid/loss: 3.0427
valid/acc: 0.0



SQL2CircuitsEstimator(a=0.001, c=0.001, id=1, workload='cardinality')

In [5]:
from skopt import BayesSearchCV
from sklearn.datasets import load_digits
from sklearn.svm import SVC
from sklearn.model_selection import train_test_split

X, y = load_digits(n_class=10, return_X_y=True)
X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=0.75, test_size=.25, random_state=0)

# log-uniform: understand as search over p = exp(x) by varying x
opt = BayesSearchCV(
    SVC(),
    {
        'C': (1e-6, 1e+6, 'log-uniform'),
        'gamma': (1e-6, 1e+1, 'log-uniform'),
        'degree': (1, 8),  # integer valued parameter
        'kernel': ['linear', 'poly', 'rbf'],  # categorical parameter
    },
    n_iter=32,
    cv=3
)

opt.fit(X_train, y_train)

print("val. score: %s" % opt.best_score_)
print("test score: %s" % opt.score(X_test, y_test))

val. score: 0.9836674090571641
test score: 0.9822222222222222
